## Debug pre_preprocessing.py (FIN)

In [2]:
from constants import SDK_PATH, DATA_PATH, WORD_EMB_PATH, CACHE_PATH
import sys

import os
import re
import mmsdk
import pickle
import argparse
import numpy as np
from tqdm import tqdm_notebook
from mmsdk import mmdatasdk as md
from subprocess import check_call, CalledProcessError

In [3]:
def avg(intervals: np.array, features: np.array) -> np.array:
    try:
        return np.average(features, axis=0)
    except:
        return features

In [4]:
def download_dataset(datasetName):
    if SDK_PATH is None:
        print("SDK path is not specified! Please specify first in constants/paths.py")
        exit(0)
    else:
        sys.path.append(SDK_PATH)

    if not os.path.exists(DATA_PATH):
        check_call(' '.join(['mkdir', '-p', DATA_PATH]), shell=True)

    if datasetName == "cmu_mosi":
        DATASET = md.cmu_mosi
    elif datasetName == "cmu_mosei":
        DATASET = md.cmu_mosei

    print(DATASET.highlevel)

    try:
        md.mmdataset(DATASET.highlevel,DATA_PATH)
    except RuntimeError:
        print("High-level features have been donwloaded previously.")

    try:
        md.mmdataset(DATASET.raw,DATA_PATH)
    except RuntimeError:
        print("Raw data have been downloaded previously.")

    try:
        md.mmdataset(DATASET.labels, DATA_PATH)
    except RuntimeError:
        print("Labels have been downloaded previously.")

    TRAINSPLIT = DATASET.standard_folds.standard_train_fold
    VALSPLIT = DATASET.standard_folds.standard_valid_fold
    TESTSPLIT = DATASET.standard_folds.standard_test_fold

    return TRAINSPLIT, VALSPLIT, TESTSPLIT

In [5]:
def prepare_save(features, dataset, TRAINSPLIT, VALSPLIT, TESTSPLIT):

    textField, visualField, speechField, labelField = features
    train = []
    val = []
    test = []
    
    EPS = 0

    # define a regular expression to extract the video ID out of the keys
    pattern = re.compile('(.*)\[.*\]')
    num_drop = 0 # a counter to count how many data points went into some processing issues

    for segment in dataset[labelField].keys():
        
        # get the video ID and the features out of the aligned dataset
        vid = re.search(pattern, segment).group(1)
        label = dataset[labelField][segment]['features']
        _words = dataset[textField][segment]['features']
        _visual = dataset[visualField][segment]['features']
        _speech = dataset[speechField][segment]['features']

        # if the sequences are not same length after alignment, there must be some problem with some modalities
        # we should drop it or inspect the data again
        if not _words.shape[0] == _visual.shape[0] == _speech.shape[0]:
            print(f"Encountered datapoint {vid} with text shape {_words.shape}, visual shape {_visual.shape}, acoustic shape {_speech.shape}")
            num_drop += 1
            continue

        # remove nan values
        label = np.nan_to_num(label)
        _visual = np.nan_to_num(_visual)
        _speech = np.nan_to_num(_speech)

        # remove speech pause tokens - this is in general helpful
        # we should remove speech pauses and corresponding visual/acoustic features together
        # otherwise modalities would no longer be aligned
        words = []
        visual = []
        speech = []
        for i, word in enumerate(_words):
            if word[0] != b'sp':
                words.append(word[0].decode('utf-8')) # SDK stores strings as bytes, decode into strings here
                visual.append(_visual[i, :])
                speech.append(_speech[i, :])

        words = np.asarray(words)
        visual = np.asarray(visual)
        speech = np.asarray(speech)

        # z-normalization per instance and remove nan/infs
        visual = np.nan_to_num((visual - visual.mean(0, keepdims=True)) / (EPS + np.std(visual, axis=0, keepdims=True)))
        speech = np.nan_to_num((speech - speech.mean(0, keepdims=True)) / (EPS + np.std(speech, axis=0, keepdims=True)))

        if vid in TRAINSPLIT:
            train.append(((words, visual, speech), label, segment))
        elif vid in VALSPLIT:
            val.append(((words, visual, speech), label, segment))
        elif vid in TESTSPLIT:
            test.append(((words, visual, speech), label, segment))
        else:
            print(f"Found video that doesn't belong to any splits: {vid}")

    print(f"Total number of {num_drop} datapoints have been dropped.")

    return train, val, test

In [6]:
def save(train, val, test, datasetName):
    allDataset = {"train":train, "val" : val, "test": test}
    with open('{}.pkl'.format(datasetName),'wb') as f:
        pickle.dump(allDataset,f)
    print("Save Complete!")

In [7]:
def main():
    TRAINSPLIT, VALSPLIT, TESTSPLIT = download_dataset('cmu_mosei')

    features = [
        'CMU_MOSEI_TimestampedWords',
        'CMU_MOSEI_VisualFacet42',
        'CMU_MOSEI_COVAREP'
    ]
    recipe = {feat: os.path.join(DATA_PATH, feat) + '.csd' for feat in features}
    
    dataset = md.mmdataset(recipe)
    dataset.align('CMU_MOSEI_TimestampedWords', collapse_functions=[avg])

    labelRecipe = {'CMU_MOSEI_Labels': os.path.join(DATA_PATH, 'CMU_MOSEI_Labels' + '.csd')}
    dataset.add_computational_sequences(labelRecipe, destination=None)
    dataset.align('CMU_MOSEI_Labels')

    features.append('CMU_MOSEI_Labels')

    train, val, test = prepare_save(features, dataset,  TRAINSPLIT, VALSPLIT, TESTSPLIT)

    save(train, val, test, 'cmu_mosei')

In [8]:
main()

{'glove_vectors': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/language/CMU_MOSEI_TimestampedWordVectors.csd', 'COVAREP': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/acoustic/CMU_MOSEI_COVAREP.csd', 'OpenFace_2': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/visual/CMU_MOSEI_VisualOpenFace2.csd', 'FACET 4.2': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/visual/CMU_MOSEI_VisualFacet42.csd'}
[2020-12-17 05:13:49.768] | Error   | ./data/CMU_MOSEI_TimestampedWordVectors.csd file already exists ...
High-level features have been donwloaded previously.
[2020-12-17 05:13:49.768] | Error   | ./data/CMU_MOSEI_TimestampedWords.csd file already exists ...
Raw data have been downloaded previously.
[2020-12-17 05:13:49.769] | Error   | ./data/CMU_MOSEI_Labels.csd file already exists ...
Labels have been downloaded previously.
[2020-12-17 05:13:49.771] | Success | Computational sequence read from file ./data/CMU_MOSEI_TimestampedWords.csd ...
[2020-12-17 05:13:49.844] | Status  | Checking

  7%|▋         | 276/3837 [00:00<00:01, 2754.69 Computational Sequence Entries/s] 

[2020-12-17 05:13:51.380] | Success | <words> computational sequence data in correct format.
[2020-12-17 05:13:51.380] | Status  | Checking the format of the metadata in <words> computational sequence ...
[2020-12-17 05:13:51.380] | Warning | <words> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 05:13:51.380] | Success | Computational sequence read from file ./data/CMU_MOSEI_VisualFacet42.csd ...
[2020-12-17 05:13:51.474] | Status  | Checking the integrity of the <FACET 4.2> computational sequence ...
[2020-12-17 05:13:51.474] | Status  | Checking the format of the data in <FACET 4.2> computational sequence ...


  7%|▋         | 273/3836 [00:00<00:01, 2724.74 Computational Sequence Entries/s] 

[2020-12-17 05:13:52.877] | Success | <FACET 4.2> computational sequence data in correct format.
[2020-12-17 05:13:52.877] | Status  | Checking the format of the metadata in <FACET 4.2> computational sequence ...
[2020-12-17 05:13:52.877] | Warning | <FACET 4.2> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 05:13:52.877] | Success | Computational sequence read from file ./data/CMU_MOSEI_COVAREP.csd ...
[2020-12-17 05:13:52.954] | Status  | Checking the integrity of the <COVAREP> computational sequence ...
[2020-12-17 05:13:52.954] | Status  | Checking the format of the data in <COVAREP> computational sequence ...


...

[2020-12-17 05:52:16.471] | Status  | Checking the format of the metadata in <CMU_MOSEI_COVAREP> computational sequence ...
[2020-12-17 05:52:16.642] | Warning | <CMU_MOSEI_COVAREP> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 05:52:16.642] | Success | Initialized empty <CMU_MOSEI_Labels> computational sequence.
[2020-12-17 05:52:16.642] | Status  | Checking the format of the data in <CMU_MOSEI_Labels> computational sequence ...
[2020-12-17 05:52:16.676] | Success | <CMU_MOSEI_Labels> computational sequence data in correct format.
[2020-12-17 05:52:16.676] | Status  | Checking the format of the metadata in <CMU_MOSEI_Labels> computational sequence ...
[2020-12-17 05:52:16.676] | Warning | <CMU_MOSEI_Labels> computational sequence does not have all the required metadata ... continuing 


/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/ipykernel_launcher.py:53: RuntimeWarning: invalid value encountered in true_divide
/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/numpy/core/_methods.py:205: RuntimeWarning: overflow encountered in multiply
  x = um.multiply(x, x, out=x)
/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/ipykernel_launcher.py:52: RuntimeWarning: invalid value encountered in true_divide
/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/numpy/core/_methods.py:160: RuntimeWarning: overflow encountered in reduce
  ret = umr_sum(arr, axis, dtype, out, keepdims)
/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/numpy/core/_methods.py:192: RuntimeWarning: overflow encountered in reduce
  arrmean = umr_sum(arr, axis, dtype, keepdims=True)


Found video that doesn't belong to any splits: -9YyBTjo1zo
Found video that doesn't belong to any splits: -9YyBTjo1zo
Found video that doesn't belong to any splits: -9YyBTjo1zo
Found video that doesn't belong to any splits: -9YyBTjo1zo
Found video that doesn't belong to any splits: -9YyBTjo1zo
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7euuU
Found video that doesn't belong to any splits: -Alixo7eu

Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AHXwnFvqYDk
Found video that doesn't belong to any splits: AcoRjVPIVmQ
Found video that doesn't belong to any splits: AcoRjVPIVmQ
Found video that doesn't belong to any splits: BgXqrxum5G4
Found video that doesn't belong to any splits: BgXqrxum5G4
Found video that doesn't belong to any splits: BgXqrxum5G4
Found video that doesn't belong to any splits: BgXqrxum5G4
Found video that doesn't belong to any splits: BgXqrxum5G4
Found video that doesn't belong to any splits: BgXqrxum5G4
Found video that doesn't belong to any splits: BgXqrxum5

KeyError: 'HuIKyKkEL0Q[0]'

In [10]:
TRAINSPLIT, VALSPLIT, TESTSPLIT = download_dataset('cmu_mosei')

{'glove_vectors': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/language/CMU_MOSEI_TimestampedWordVectors.csd', 'COVAREP': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/acoustic/CMU_MOSEI_COVAREP.csd', 'OpenFace_2': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/visual/CMU_MOSEI_VisualOpenFace2.csd', 'FACET 4.2': 'http://immortal.multicomp.cs.cmu.edu/CMU-MOSEI/visual/CMU_MOSEI_VisualFacet42.csd'}
[2020-12-17 05:58:37.163] | Error   | ./data/CMU_MOSEI_TimestampedWordVectors.csd file already exists ...
High-level features have been donwloaded previously.
[2020-12-17 05:58:37.163] | Error   | ./data/CMU_MOSEI_TimestampedWords.csd file already exists ...
Raw data have been downloaded previously.
[2020-12-17 05:58:37.164] | Error   | ./data/CMU_MOSEI_Labels.csd file already exists ...
Labels have been downloaded previously.


In [11]:
features = [
    'CMU_MOSEI_TimestampedWords',
    'CMU_MOSEI_VisualFacet42',
    'CMU_MOSEI_COVAREP'
]
recipe = {feat: os.path.join(DATA_PATH, feat) + '.csd' for feat in features}

dataset = md.mmdataset(recipe)
dataset.align('CMU_MOSEI_TimestampedWords', collapse_functions=[avg])

[2020-12-17 05:58:48.227] | Success | Computational sequence read from file ./data/CMU_MOSEI_TimestampedWords.csd ...


 14%|█▍        | 537/3837 [00:00<00:01, 2697.91 Computational Sequence Entries/s]

[2020-12-17 05:58:48.694] | Status  | Checking the integrity of the <words> computational sequence ...
[2020-12-17 05:58:48.694] | Status  | Checking the format of the data in <words> computational sequence ...


  7%|▋         | 270/3837 [00:00<00:01, 2697.16 Computational Sequence Entries/s] 

[2020-12-17 05:58:50.165] | Success | <words> computational sequence data in correct format.
[2020-12-17 05:58:50.165] | Status  | Checking the format of the metadata in <words> computational sequence ...
[2020-12-17 05:58:50.165] | Warning | <words> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 05:58:50.165] | Success | Computational sequence read from file ./data/CMU_MOSEI_VisualFacet42.csd ...
[2020-12-17 05:58:50.245] | Status  | Checking the integrity of the <FACET 4.2> computational sequence ...
[2020-12-17 05:58:50.245] | Status  | Checking the format of the data in <FACET 4.2> computational sequence ...


...

  7%|▋         | 77354/1082652 [00:00<00:01, 773535.20 Computational Sequence Entries/s]  

[2020-12-17 06:33:15.202] | Success | <CMU_MOSEI_TimestampedWords> computational sequence data in correct format.
[2020-12-17 06:33:15.202] | Status  | Checking the format of the metadata in <CMU_MOSEI_TimestampedWords> computational sequence ...
[2020-12-17 06:33:15.202] | Warning | <CMU_MOSEI_TimestampedWords> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 06:33:15.202] | Success | Initialized empty <CMU_MOSEI_VisualFacet42> computational sequence.
[2020-12-17 06:33:15.202] | Status  | Checking the format of the data in <CMU_MOSEI_VisualFacet42> computational sequence ...


  7%|▋         | 79528/1083861 [00:00<00:01, 795275.07 Computational Sequence Entries/s]  

[2020-12-17 06:33:16.487] | Success | <CMU_MOSEI_VisualFacet42> computational sequence data in correct format.
[2020-12-17 06:33:16.488] | Status  | Checking the format of the metadata in <CMU_MOSEI_VisualFacet42> computational sequence ...
[2020-12-17 06:33:16.488] | Warning | <CMU_MOSEI_VisualFacet42> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 06:33:16.488] | Success | Initialized empty <CMU_MOSEI_COVAREP> computational sequence.
[2020-12-17 06:33:16.488] | Status  | Checking the format of the data in <CMU_MOSEI_COVAREP> computational sequence ...


[2020-12-17 06:33:17.775] | Success | <CMU_MOSEI_COVAREP> computational sequence data in correct format.
[2020-12-17 06:33:17.775] | Status  | Checking the format of the metadata in <CMU_MOSEI_COVAREP> computational sequence ...
[2020-12-17 06:33:17.776] | Warning | <CMU_MOSEI_COVAREP> computational sequence does not have all the required metadata ... continuing 


In [17]:
labelRecipe = {'CMU_MOSEI_Labels': os.path.join(DATA_PATH, 'CMU_MOSEI_Labels' + '.csd')}
dataset.add_computational_sequences(labelRecipe, destination=None)
dataset.align('CMU_MOSEI_Labels')

features.append('CMU_MOSEI_Labels')

  8%|▊         | 256/3293 [00:00<00:01, 2552.44 Computational Sequence Entries/s]

[2020-12-17 06:41:56.364] | Warning | Dataset already contains <CMU_MOSEI_Labels> computational sequence ...
[2020-12-17 06:41:56.364] | Success | Computational sequence read from file ./data/CMU_MOSEI_Labels.csd ...
[2020-12-17 06:41:56.462] | Status  | Checking the integrity of the <All Labels> computational sequence ...
[2020-12-17 06:41:56.462] | Status  | Checking the format of the data in <All Labels> computational sequence ...


[2020-12-17 06:41:57.716] | Success | <All Labels> computational sequence data in correct format.
[2020-12-17 06:41:57.716] | Status  | Checking the format of the metadata in <All Labels> computational sequence ...
[2020-12-17 06:41:57.716] | Warning | <All Labels> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 06:41:57.716] | Status  | Unify was called ...
[2020-12-17 06:41:58.978] | Warning | 233940 entry is not shared among all sequences, removing it ...
[2020-12-17 06:41:59.372] | Warning | 191616 entry is not shared among all sequences, removing it ...
[2020-12-17 06:41:59.772] | Warning | PEBwwe0PLZ8 entry is not shared among all sequences, removing it ...
[2020-12-17 06:42:00.154] | Warning | 73360 entry is not shared among all sequences, removing it ...
[2020-12-17 06:42:00.547] | Warning | 220832 entry is not shared among all sequences, removing it ...
[2020-12-17 06:42:00.938] | Warning | 270993 entry is not shared among all sequenc

Aligning --qXJuDtHPw:   0%|          | 0/1 [00:00<?, ? Segments/s]
                                                                  
Aligning -3g5yACwYnA:   0%|          | 0/6 [00:00<?, ? Segments/s]
                                                                  
Aligning -3nNcZdcdvU:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning -571d8cVauQ:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning -6rXp3zJ3kc:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning -9YyBTjo1zo:   0%|          | 0/5 [00:00<?, ? Segments/s]
                                                                  
Aligning -9y-fZ3swSY:   0%|          | 0/8 [00:00<?, ? Segments/s]
                                                                  
Aligning -AUZQgSxyPQ:   0%|          | 0/1 [00:00<?, ? Segment

[2020-12-17 06:42:10.233] | Status  | Pre-alignment done for <CMU_MOSEI_VisualFacet42> ...
[2020-12-17 06:42:10.293] | Status  | Alignment starting ...


...

                                                                  
Aligning vA68fTqDars:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning vC9oWzTU71s:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning vCWpKubBbcw:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning vGkIaClHKDg:   0%|          | 0/11 [00:00<?, ? Segments/s]
                                                                   
Aligning vGxqVh_kJdo:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning vHzbn_YW76s:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning vI5JH0daNsM:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                            

Aligning x-oexIBWwR4:   0%|          | 0/9 [00:00<?, ? Segments/s]
                                                                  
Aligning x-zGBp7axao:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning x0rLwBIocuI:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning x2lOwQaAn4g:   0%|          | 0/5 [00:00<?, ? Segments/s]
                                                                  
Aligning x2n19Cn96aw:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning x5xF4yu9Bos:   0%|          | 0/10 [00:00<?, ? Segments/s]
                                                                   
Aligning x7ZR70cTa84:   0%|          | 0/2 [00:00<?, ? Segments/s]
                                                                  
Aligning x8UZQkN52o4:   0%|          | 0/8 [00:00<?, ? Segme

Aligning yrIXBklJ5YQ:   0%|          | 0/6 [00:00<?, ? Segments/s]
                                                                  
Aligning ysGFcG_PI5I:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning yt9GpittX4U:   0%|          | 0/1 [00:00<?, ? Segments/s]
                                                                  
Aligning ytXVSpPfKwA:   0%|          | 0/4 [00:00<?, ? Segments/s]
                                                                  
Aligning yuwvVTnsDjc:   0%|          | 0/6 [00:00<?, ? Segments/s]
                                                                  
Aligning yyToAEoUuek:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning yzCHa2qchpg:   0%|          | 0/3 [00:00<?, ? Segments/s]
                                                                  
Aligning z-bupzylxEc:   0%|          | 0/1 [00:00<?, ? Segment

[2020-12-17 06:42:43.212] | Success | Alignment to <CMU_MOSEI_Labels> complete.
[2020-12-17 06:42:43.212] | Status  | Replacing dataset content with aligned computational sequences
[2020-12-17 06:42:45.124] | Success | Initialized empty <CMU_MOSEI_TimestampedWords> computational sequence.
[2020-12-17 06:42:45.126] | Status  | Checking the format of the data in <CMU_MOSEI_TimestampedWords> computational sequence ...
[2020-12-17 06:42:45.172] | Success | <CMU_MOSEI_TimestampedWords> computational sequence data in correct format.
[2020-12-17 06:42:45.174] | Status  | Checking the format of the metadata in <CMU_MOSEI_TimestampedWords> computational sequence ...
[2020-12-17 06:42:45.175] | Warning | <CMU_MOSEI_TimestampedWords> computational sequence does not have all the required metadata ... continuing 
[2020-12-17 06:42:45.176] | Success | Initialized empty <CMU_MOSEI_VisualFacet42> computational sequence.
[2020-12-17 06:42:45.180] | Status  | Checking the format of the data in <CMU_MOSE

[2020-12-17 06:42:45.610] | Success | <CMU_MOSEI_Labels> computational sequence data in correct format.
[2020-12-17 06:42:45.610] | Status  | Checking the format of the metadata in <CMU_MOSEI_Labels> computational sequence ...
[2020-12-17 06:42:45.610] | Warning | <CMU_MOSEI_Labels> computational sequence does not have all the required metadata ... continuing 


In [23]:

textField, visualField, speechField, labelField = features
train = []
val = []
test = []

EPS = 0

# define a regular expression to extract the video ID out of the keys
pattern = re.compile('(.*)\[.*\]')
num_drop = 0 # a counter to count how many data points went into some processing issues

for segment in dataset[labelField].keys():

    # get the video ID and the features out of the aligned dataset
    vid = re.search(pattern, segment).group(1)
    try:
        label = dataset[labelField][segment]
        _words = dataset[textField][segment]
        _visual = dataset[visualField][segment]
        _speech = dataset[speechField][segment]
    except:
        print(f"[Segment]Found video that doesn't belong to any splits: {segment}")
        num_drop+=1
        continue
        
    label = label['features']
    _words = _words['features']
    _visual = _visual['features']
    _speech = _speech['features']

    # if the sequences are not same length after alignment, there must be some problem with some modalities
    # we should drop it or inspect the data again
    if not _words.shape[0] == _visual.shape[0] == _speech.shape[0]:
        print(f"Encountered datapoint {vid} with text shape {_words.shape}, visual shape {_visual.shape}, acoustic shape {_speech.shape}")
        num_drop += 1
        continue

    # remove nan values
    label = np.nan_to_num(label)
    _visual = np.nan_to_num(_visual)
    _speech = np.nan_to_num(_speech)

    # remove speech pause tokens - this is in general helpful
    # we should remove speech pauses and corresponding visual/acoustic features together
    # otherwise modalities would no longer be aligned
    words = []
    visual = []
    speech = []
    for i, word in enumerate(_words):
        if word[0] != b'sp':
            words.append(word[0].decode('utf-8')) # SDK stores strings as bytes, decode into strings here
            visual.append(_visual[i, :])
            speech.append(_speech[i, :])

    words = np.asarray(words)
    visual = np.asarray(visual)
    speech = np.asarray(speech)

    # z-normalization per instance and remove nan/infs
    visual = np.nan_to_num((visual - visual.mean(0, keepdims=True)) / (EPS + np.std(visual, axis=0, keepdims=True)))
    speech = np.nan_to_num((speech - speech.mean(0, keepdims=True)) / (EPS + np.std(speech, axis=0, keepdims=True)))

    if vid in TRAINSPLIT:
        train.append(((words, visual, speech), label, segment))
    elif vid in VALSPLIT:
        val.append(((words, visual, speech), label, segment))
    elif vid in TESTSPLIT:
        test.append(((words, visual, speech), label, segment))
    else:
        print(f"[Videosplit]Found video that doesn't belong to any splits: {vid}")

print(f"Total number of {num_drop} datapoints have been dropped.")

/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/ipykernel_launcher.py:61: RuntimeWarning: invalid value encountered in true_divide
/home/kkh/anaconda3/envs/msa/lib/python3.6/site-packages/ipykernel_launcher.py:60: RuntimeWarning: invalid value encountered in true_divide


[Videosplit]Found video that doesn't belong to any splits: -9YyBTjo1zo
[Videosplit]Found video that doesn't belong to any splits: -9YyBTjo1zo
[Videosplit]Found video that doesn't belong to any splits: -9YyBTjo1zo
[Videosplit]Found video that doesn't belong to any splits: -9YyBTjo1zo
[Videosplit]Found video that doesn't belong to any splits: -9YyBTjo1zo
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Videosplit]Found video that doesn't belong to any splits: -Alixo7euuU
[Video

Encountered datapoint 69824 with text shape (7, 1), visual shape (6, 35), acoustic shape (7, 74)
[Videosplit]Found video that doesn't belong to any splits: 6ywl-j2-e-s
[Videosplit]Found video that doesn't belong to any splits: 6ywl-j2-e-s
[Videosplit]Found video that doesn't belong to any splits: 7BFhRPlSOf0
[Videosplit]Found video that doesn't belong to any splits: 7BFhRPlSOf0
[Videosplit]Found video that doesn't belong to any splits: 7BFhRPlSOf0
[Videosplit]Found video that doesn't belong to any splits: 7BFhRPlSOf0
[Videosplit]Found video that doesn't belong to any splits: 7BFhRPlSOf0
Encountered datapoint 8f_lBxZgDb0 with text shape (55, 1), visual shape (54, 35), acoustic shape (55, 74)
[Videosplit]Found video that doesn't belong to any splits: 8vpoQ5UVpXE
[Videosplit]Found video that doesn't belong to any splits: 8vpoQ5UVpXE
[Videosplit]Found video that doesn't belong to any splits: 8vpoQ5UVpXE
[Videosplit]Found video that doesn't belong to any splits: 8vpoQ5UVpXE
[Videosplit]Foun

[Videosplit]Found video that doesn't belong to any splits: XnPnlRQXSkM
[Videosplit]Found video that doesn't belong to any splits: XnPnlRQXSkM
[Videosplit]Found video that doesn't belong to any splits: XnPnlRQXSkM
[Videosplit]Found video that doesn't belong to any splits: XnPnlRQXSkM
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
[Videosplit]Found video that doesn't belong to any splits: ZXQkyX6prBQ
Encountered datapoint aa0J1AXSseY with text shape (32, 1), visual shape (23, 35), acoustic shape (32, 74)
[Segment]Found video that doesn't belong to any splits: aa0J1AXSseY[4]
[Segment]Found video that doesn't belong t

[Videosplit]Found video that doesn't belong to any splits: ptp-kfn4vWY
[Videosplit]Found video that doesn't belong to any splits: ptp-kfn4vWY
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: qYC3gN1AkOA
[Videosplit]Found video that doesn't belong to any splits: rKyXU0ls5aQ
[Videosplit]Found video that doesn't belong to any splits: rKyXU0ls5aQ
[Videosplit]Found video that doesn't belong to any splits: rKyXU0ls5aQ
[Videosplit]Found video that doesn't belong to any splits: rKyXU0ls5aQ
[Video

In [30]:
train[0]

((array(['key', 'is', 'part', 'of', 'the', 'people', 'that', 'we', 'use',
         'to', 'solve', 'those', 'issues', 'whether', "it's", 'stretch',
         'or', 'outdoor', 'resistance', 'or', 'abrasions', 'or',
         'different', 'technical', 'aspects', 'that', 'we', 'really',
         'need', 'to', 'solve', 'to', 'get', 'into', 'new', 'markets',
         "they've", 'been', 'able', 'to', 'bring', 'solutions'],
        dtype='<U10'),
  array([[ 2.56679929e-03, -1.55861712e+00,  3.23883057e+00, ...,
          -5.30693412e-01, -2.19982177e-01, -3.39928865e-01],
         [-9.00127828e-01,  4.08462316e-01,  4.10952941e-02, ...,
           3.32075864e-01,  1.19635546e+00, -1.06940329e+00],
         [ 1.53208494e+00, -1.17383730e+00,  5.54638326e-01, ...,
           1.13103139e+00,  1.12885392e+00, -1.34822011e+00],
         ...,
         [ 3.79706621e-01, -1.02476335e+00, -1.28982687e+00, ...,
          -6.92572296e-02,  5.84073551e-02,  3.85742486e-01],
         [ 7.13733375e-01, -2.568

In [24]:
save(train, val, test, 'cmu_mosei')

Save Complete!


In [25]:
!python train.py

  File "train.py", line 43
    p for n, p in param_optimizer if not and(nd in n for nd in no_decay)
                                           ^
SyntaxError: invalid syntax


In [32]:
import pickle
with open("cmu_mosei.pkl",'br') as fr:
    data = pickle.load(fr)

In [36]:
data['train'][0]

((array(['key', 'is', 'part', 'of', 'the', 'people', 'that', 'we', 'use',
         'to', 'solve', 'those', 'issues', 'whether', "it's", 'stretch',
         'or', 'outdoor', 'resistance', 'or', 'abrasions', 'or',
         'different', 'technical', 'aspects', 'that', 'we', 'really',
         'need', 'to', 'solve', 'to', 'get', 'into', 'new', 'markets',
         "they've", 'been', 'able', 'to', 'bring', 'solutions'],
        dtype='<U10'),
  array([[ 2.56679929e-03, -1.55861712e+00,  3.23883057e+00, ...,
          -5.30693412e-01, -2.19982177e-01, -3.39928865e-01],
         [-9.00127828e-01,  4.08462316e-01,  4.10952941e-02, ...,
           3.32075864e-01,  1.19635546e+00, -1.06940329e+00],
         [ 1.53208494e+00, -1.17383730e+00,  5.54638326e-01, ...,
           1.13103139e+00,  1.12885392e+00, -1.34822011e+00],
         ...,
         [ 3.79706621e-01, -1.02476335e+00, -1.28982687e+00, ...,
          -6.92572296e-02,  5.84073551e-02,  3.85742486e-01],
         [ 7.13733375e-01, -2.568

## Debug makeDataset in train.py (FIN)
sentencepiece downgrade to 0.1.91

In [1]:
from transformers.modeling_bert import BertModel
from transformers import BertTokenizer

import pickle
import numpy as np

In [4]:
with open("cmu_mosei.pkl",'br') as fr:
    data = pickle.load(fr)

trainData = data["train"]
valData = data["val"]
testData = data["test"]

In [9]:
def get_tokenizer(model):
    if model == "bert-base-uncased":
        return BertTokenizer.from_pretrained(model)
    elif model == "bert-large-uncased":
        return BertTokenizer.from_pretrained(model)
    else:
        raise ValueError(
            "Expected 'bert-base-uncased' or 'bert-large-uncased', but get {}".format(model)
            )

In [10]:
tokenizer = get_tokenizer('bert-base-uncased')

In [11]:
def convertTofeatures(samples,tokenizer):
    features = []
    for idx, sample in enumerate(samples):
        (words,visual,speech), label, segment = sample
        
        tokens, inversions = [],[]
        for i, word in enumerate(list(words)):
            tokenized = tokenizer.tokenize(word)
            tokens.extend(tokenized)
            #Because of '##__' case.
            inversions.extend([i]*len(tokenized))
        
        assert len(tokens) == len(inversions)
        
        newVisual, newSpeech = [],[]
        for inv in inversions:
            newVisual.append(visual[inv,:])
            newSpeech.append(speech[inv,:])
        
        visual = np.array(newVisual)
        speech = np.array(newSpeech)
        
        features.append(
            ((words,visual,speech),
            label,
            segment)
        )
    return features

In [15]:
features = convertTofeatures(trainData,tokenizer)

In [ ]:
config = BertModel.from_pretrained('bert-base-uncased').config

In [1]:
from transformers.configuration_bert import BertConfig
BertConfig =BertConfig()

In [ ]:
from transformers.modeling_bert import BertEmbeddings
embeddings = BertEmbeddings(BertConfig)

### Debug add u10 and u10 (FIN)
np.array to list로 해결

In [2]:
from transformers import BertTokenizer

import pickle
import numpy as np

In [3]:
with open("cmu_mosei.pkl",'br') as fr:
    data = pickle.load(fr)

trainData = data["train"]
valData = data["val"]
testData = data["test"]

In [4]:
def get_tokenizer(model):
    if model == "bert-base-uncased":
        return BertTokenizer.from_pretrained(model)
    elif model == "bert-large-uncased":
        return BertTokenizer.from_pretrained(model)
    else:
        raise ValueError(
            "Expected 'bert-base-uncased' or 'bert-large-uncased', but get {}".format(model)
            )

In [5]:
tokenizer = get_tokenizer('bert-base-uncased')

In [6]:
def convertTofeatures(samples,tokenizer):
    features = []
    for idx, sample in enumerate(samples):
        (words,visual,speech), label, segment = sample
        
        tokens, inversions = [],[]
        for i, word in enumerate(list(words)):
            tokenized = tokenizer.tokenize(word)
            tokens.extend(tokenized)
            #Because of '##__' case.
            inversions.extend([i]*len(tokenized))
        
        assert len(tokens) == len(inversions)
        
        newVisual, newSpeech = [],[]
        for inv in inversions:
            newVisual.append(visual[inv,:])
            newSpeech.append(speech[inv,:])
        
        visual = np.array(newVisual)
        speech = np.array(newSpeech)
        
        features.append(
            ((list(words),visual,speech),
            label,
            segment)
        )
    return features

In [7]:
features = convertTofeatures(trainData,tokenizer)

In [24]:
[tokenizer.sep_token]+list(features[0][0][0])

['[SEP]',
 'key',
 'is',
 'part',
 'of',
 'the',
 'people',
 'that',
 'we',
 'use',
 'to',
 'solve',
 'those',
 'issues',
 'whether',
 "it's",
 'stretch',
 'or',
 'outdoor',
 'resistance',
 'or',
 'abrasions',
 'or',
 'different',
 'technical',
 'aspects',
 'that',
 'we',
 'really',
 'need',
 'to',
 'solve',
 'to',
 'get',
 'into',
 'new',
 'markets',
 "they've",
 'been',
 'able',
 'to',
 'bring',
 'solutions']

In [26]:
tokenizer.convert_tokens_to_ids(features[0][0][0])

[3145,
 2003,
 2112,
 1997,
 1996,
 2111,
 2008,
 2057,
 2224,
 2000,
 9611,
 2216,
 3314,
 3251,
 100,
 7683,
 2030,
 7254,
 5012,
 2030,
 100,
 2030,
 2367,
 4087,
 5919,
 2008,
 2057,
 2428,
 2342,
 2000,
 9611,
 2000,
 2131,
 2046,
 2047,
 6089,
 100,
 2042,
 2583,
 2000,
 3288,
 7300]

In [27]:
tokenizer.convert_tokens_to_ids([tokenizer.sep_token]+list(features[0][0][0]))

[102,
 3145,
 2003,
 2112,
 1997,
 1996,
 2111,
 2008,
 2057,
 2224,
 2000,
 9611,
 2216,
 3314,
 3251,
 100,
 7683,
 2030,
 7254,
 5012,
 2030,
 100,
 2030,
 2367,
 4087,
 5919,
 2008,
 2057,
 2428,
 2342,
 2000,
 9611,
 2000,
 2131,
 2046,
 2047,
 6089,
 100,
 2042,
 2583,
 2000,
 3288,
 7300]

In [35]:
firstTokenTypeIds =  np.zeros(10+2)
secondTokenTypeIds =  np.ones(20+1)
np.concatenate((firstTokenTypeIds,secondTokenTypeIds))

array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 1., 1., 1., 1.,
       1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.])

In [1]:
import torch

In [4]:
torch.ones((1,78))*100

tensor([[100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100.,
         100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100.,
         100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100.,
         100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100.,
         100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100.,
         100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100., 100.,
         100., 100., 100., 100., 100., 100.]])

In [1]:
import torch

In [2]:
a = [torch.ones(7),torch.zeros(7)]

In [3]:
a

[tensor([1., 1., 1., 1., 1., 1., 1.]), tensor([0., 0., 0., 0., 0., 0., 0.])]

In [4]:
torch.tensor(a)

ValueError: only one element tensors can be converted to Python scalars

In [9]:
b=torch.zeros((10,7))

In [12]:
b[0] = torch.ones(7)

In [13]:
b

tensor([[1., 1., 1., 1., 1., 1., 1.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.],
        [0., 0., 0., 0., 0., 0., 0.]])

In [19]:
any(torch.tensor([0,0,0,0]),torch.tensor([0,0,0,1]))

TypeError: any() takes exactly one argument (2 given)

In [21]:
a = [torch.tensor(1),torch.tensor(0)]

In [22]:
torch.tensor(a)

tensor([1, 0])

In [23]:
torch.tensor([[0,1],[1,0]])

tensor([[0, 1],
        [1, 0]])

In [24]:
inputs = torch.randn(3, 5, requires_grad=True)
targets = torch.empty(3, dtype=torch.long).random_(5)

In [25]:
inputs

tensor([[-0.0951, -1.5939, -0.3717,  0.4398,  0.1921],
        [ 0.8878, -0.3330, -1.2348,  1.3694,  1.1019],
        [ 1.7713, -1.5540,  0.7764,  1.4884, -0.2774]], requires_grad=True)

In [26]:
targets

tensor([2, 3, 3])

In [15]:
import pickle

with open("cmu_mosei.pkl",'br') as fr:
    data2 = pickle.load(fr)

In [25]:
for d in data['train']:
    print(abs(d[1][0]))

[1.        0.6666667 0.6666667 0.        0.        0.        0.6666667]
[0.6666667 0.        0.        0.        0.        0.        0.       ]
[0.         0.6666667  0.6666667  0.         0.         0.
 0.33333334]
[0.         0.33333334 0.33333334 0.         0.         0.
 0.        ]
[1.        0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667  0.         0.6666667  0.         0.         0.
 0.33333334]
[0.33333334 1.6666666  0.         0.         0.         0.
 0.        ]
[1.        2.3333333 0.        0.        0.        0.        0.       ]
[0.        1.6666666 0.        0.        0.        0.        0.       ]
[0. 0. 0. 0. 0. 0. 0.]
[0.6666667  0.         0.33333334 0.         0.         0.
 0.        ]
[0. 0. 0. 0. 0. 0. 0.]
[0.33333334 0.         0.33333334 0.         0.         0.33333334
 0.        ]
[2.        0.        0.6666667 0.        0.        0.6666667 0.       ]
[1. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0.]
[0.6666667 0.6666667 0.        0.   

 0.        ]
[1.        0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667  0.33333334 0.         0.         0.33333334 0.
 0.        ]
[0.6666667  0.33333334 0.         0.         0.33333334 0.
 0.        ]
[0. 0. 0. 0. 0. 0. 0.]
[0.6666667 0.        0.        0.        0.        0.        0.       ]
[1.3333334 1.3333334 0.        0.        0.        0.        0.       ]
[1.         1.         0.         0.         0.33333334 0.
 0.        ]
[2.        2.3333333 0.        0.        0.        0.        0.       ]
[2.3333333 2.        0.        0.        0.        0.        0.       ]
[1.3333334  0.33333334 0.33333334 0.         0.         0.
 0.        ]
[1.        0.6666667 0.        0.        0.        0.        0.       ]
[1.         0.6666667  0.33333334 0.6666667  0.         1.3333334
 0.        ]
[0.6666667  0.33333334 0.         0.6666667  0.         0.33333334
 0.        ]
[0. 0. 0. 0. 0. 0. 0.]
[0.33333334 0.         0.         0.33333334 0.         0.
 0.

[3.        0.        0.        2.6666667 0.        1.6666666 0.       ]
[2.6666667 0.        0.        2.3333333 0.        1.6666666 0.       ]
[2.6666667  0.         0.33333334 2.3333333  0.6666667  0.6666667
 0.        ]
[3. 0. 0. 2. 0. 2. 0.]
[2.3333333 0.        0.        1.3333334 0.        0.        0.       ]
[2.3333333 0.        0.        2.3333333 0.        0.        0.       ]
[1.6666666 0.        0.        2.        0.        0.6666667 0.       ]
[1. 0. 0. 2. 0. 0. 0.]
[1.3333334 0.        0.        1.6666666 0.        0.        0.       ]
[2.        0.        0.        1.6666666 0.        0.6666667 0.       ]
[3.        0.        0.        2.6666667 0.        0.6666667 0.       ]
[2.6666667 0.        0.        2.        0.6666667 1.        0.       ]
[1.3333334 0.        0.6666667 2.        0.        0.6666667 0.       ]
[2.6666667 0.        0.        2.        0.        1.        0.       ]
[2.6666667 0.        0.        1.6666666 0.        0.        0.       ]
[1.6666666 

 0.        ]
[1.         0.         0.         0.33333334 0.         0.
 0.        ]
[2.        0.        0.        1.        0.        0.6666667 0.       ]
[1.6666666  0.         1.         0.33333334 0.         0.33333334
 0.        ]
[2.         0.         0.         1.3333334  0.         0.33333334
 0.        ]
[0.         0.         0.         1.3333334  0.         0.33333334
 0.        ]
[1.         0.         0.6666667  0.33333334 0.         0.
 0.        ]
[1.6666666 0.        0.        1.        0.        0.        0.       ]
[2.6666667 0.        0.        2.        0.        1.        0.       ]
[2.6666667 0.        0.        2.3333333 0.        1.6666666 0.       ]
[1.3333334  0.         0.         1.         0.         0.33333334
 0.        ]
[2.        0.        0.6666667 1.        0.        1.        0.       ]
[2.6666667 0.        0.        1.6666666 0.        0.6666667 0.       ]
[1.6666666 0.        0.        1.6666666 0.        1.        0.       ]
[2.        0.      

 0.        ]
[0. 0. 0. 0. 0. 0. 0.]
[1.         0.         0.33333334 0.         0.         0.33333334
 0.        ]
[1.         0.33333334 0.         0.         0.         0.
 0.        ]
[0.6666667  0.         0.         0.         0.         0.33333334
 0.        ]
[1.3333334 2.        0.        0.        0.        0.        1.       ]
[1.        1.        0.        0.6666667 0.        0.        0.6666667]
[1.3333334 2.        0.        0.        0.        0.        0.       ]
[1.        1.3333334 0.        0.        0.        0.        0.       ]
[2.3333333 2.        0.        0.        0.        0.        0.       ]
[0. 0. 0. 0. 0. 0. 0.]
[0.         0.         0.         0.         0.         0.33333334
 0.        ]
[0.33333334 0.33333334 0.         0.         0.         0.33333334
 0.        ]
[0.         0.33333334 0.6666667  0.         0.         0.
 0.        ]
[0.33333334 0.         0.         0.         0.         0.33333334
 0.        ]
[0.         0.         0.33333334 0. 

...

 0.33333334]
[0.         0.33333334 0.33333334 0.         0.         0.
 0.33333334]
[1.3333334 0.        1.3333334 0.        0.        0.6666667 0.       ]
[0.6666667  0.         0.         1.3333334  0.         0.33333334
 0.33333334]
[0.6666667  0.         0.         1.3333334  0.         0.33333334
 0.33333334]
[0.33333334 0.         0.         0.33333334 0.         0.
 0.        ]
[1.3333334 0.        0.        1.6666666 0.        0.        0.       ]
[0.         0.         0.         0.33333334 0.         0.
 0.        ]
[0.6666667 0.        0.        2.3333333 0.        0.        0.       ]
[1.3333334  0.         0.         0.33333334 0.         0.33333334
 0.        ]
[1.3333334  0.         0.         0.6666667  0.         0.33333334
 0.        ]
[2.6666667 0.        1.        2.3333333 0.        1.3333334 0.       ]
[2.3333333 0.        0.        1.3333334 0.        0.6666667 0.       ]
[0.6666667 0.        0.        0.6666667 0.        0.        0.       ]
[0.6666667  0.     

[0.6666667 0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667 0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667 0.6666667 0.        0.        0.        0.        0.       ]
[2. 0. 0. 0. 0. 0. 0.]
[1.3333334  0.33333334 0.         0.         0.         0.
 0.        ]
[1.         0.6666667  0.         0.         0.         0.
 0.33333334]
[0.6666667 1.        0.        0.        0.        0.        0.       ]
[1.6666666 0.6666667 0.        0.        0.        0.        0.6666667]
[0.        1.3333334 0.        0.6666667 0.6666667 1.3333334 0.       ]
[0.33333334 1.         0.         0.6666667  1.6666666  0.6666667
 0.        ]
[0.6666667 2.3333333 0.        0.        0.        0.        0.6666667]
[0.33333334 2.         0.         0.         0.         0.
 0.        ]
[0.6666667 1.        0.        0.        0.        0.        0.       ]
[1.6666666  0.         0.         0.33333334 0.         0.6666667
 0.        ]
[1.         0.         0.  

 0.        ]
[0.6666667  0.         0.         0.         0.         0.33333334
 0.        ]
[0.6666667 0.5       0.        0.        0.        0.        0.       ]
[0.33333334 0.33333334 0.         0.         0.33333334 0.
 0.        ]
[0.33333334 0.         0.         0.         0.         0.
 0.        ]
[0.33333334 0.16666667 0.         0.         0.16666667 0.
 0.        ]
[0.         0.33333334 0.         0.         0.         0.
 0.        ]
[0.5        0.16666667 0.         0.         0.         0.
 0.        ]
[0.16666667 0.         0.         0.         0.         0.
 0.        ]
[1.3333334 0.6666667 0.        0.        0.        0.        0.       ]
[0.16666667 0.16666667 0.         0.         0.         0.
 0.        ]
[1.         0.33333334 0.         0.         0.         0.
 0.        ]
[0.         0.         0.         0.33333334 0.         0.33333334
 0.33333334]
[0. 0. 0. 0. 0. 0. 0.]
[0.16666667 0.         0.         0.         0.         0.
 0.        ]
[0.16666667 

 0.        ]
[0.33333334 0.33333334 0.33333334 0.         0.33333334 0.33333334
 0.33333334]
[0.33333334 0.         0.6666667  0.         0.         0.
 0.        ]
[0.6666667  0.33333334 0.         0.         0.         0.
 0.        ]
[0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0.]
[0.        0.        0.6666667 0.        0.        0.        0.       ]
[2.3333333  2.         0.33333334 0.33333334 0.         0.33333334
 0.        ]
[0.33333334 0.         0.6666667  0.         0.         0.
 0.        ]
[0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0.]
[0.33333334 0.         0.         0.         0.         0.
 0.        ]
[0.        0.        0.6666667 0.        0.        0.        0.       ]
[0.33333334 0.         0.6666667  0.         0.         0.
 0.        ]
[0.6666667 0.        0.        0.        0.        0.        0.       ]
[1.        0.        0.6666667 0.        0.        0.        0.       ]
[0. 0. 0. 0. 0. 0. 0.]
[0.33333334 0.3333

 0.        ]
[0.33333334 0.         0.         0.         0.         0.
 0.        ]
[0.33333334 0.33333334 0.         0.         0.         0.
 0.        ]
[0.6666667 0.        0.        0.        0.        0.        0.       ]
[1.        0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667  0.33333334 0.         0.         0.         0.
 0.        ]
[0.33333334 0.         0.6666667  0.         0.         0.
 0.        ]
[1.3333334  0.6666667  0.33333334 0.         0.         0.
 0.33333334]
[2.3333333 0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667 0.        0.        0.        0.        0.        0.       ]
[0.         0.33333334 0.         0.         0.         0.
 0.        ]
[0.6666667 0.6666667 0.        0.        0.        0.        0.       ]
[0.6666667  0.         0.         0.         0.33333334 0.
 0.33333334]
[0.33333334 0.         0.33333334 0.         0.6666667  0.
 0.        ]
[0.33333334 0.         0.         0.         0.    

In [17]:
data2['train'][0][1]

array([[1.       , 0.6666667, 0.6666667, 0.       , 0.       , 0.       ,
        0.6666667]], dtype=float32)

In [44]:
import pickle

with open("cmu_mosi.pkl",'br') as fr:
    data = pickle.load(fr)

In [47]:
a=dict()
for i in range(len(data['train'])):
    if a.get(data['train'][i][1][0][0]):
        a[data['train'][i][1][0][0]]+=1
    else:
        a[data['train'][i][1][0][0]]=1

In [48]:
a

{2.4: 36,
 -0.8: 48,
 -1.0: 62,
 -1.75: 3,
 0.0: 53,
 0.8: 40,
 0.2: 37,
 -1.2: 36,
 -0.5: 14,
 2.2: 67,
 1.8: 66,
 -0.4: 44,
 -2.8: 9,
 -0.2: 37,
 -1.4: 38,
 -0.6: 29,
 0.4: 37,
 1.25: 1,
 1.4: 63,
 0.6: 40,
 -2.0: 53,
 2.0: 77,
 2.6: 26,
 1.6: 62,
 1.0: 38,
 -1.8: 39,
 -1.6: 56,
 -1.25: 6,
 -2.4: 12,
 1.2: 41,
 0.5: 9,
 -1.5: 5,
 0.33333334: 1,
 0.25: 8,
 2.8: 16,
 3.0: 4,
 -2.6: 12,
 -2.2: 29,
 -0.33333334: 2,
 -0.6666667: 2,
 -0.25: 5,
 -0.75: 6,
 1.75: 3,
 0.6666667: 1,
 -2.25: 1,
 1.5: 2,
 0.75: 2,
 1.3333334: 1,
 -3.0: 3,
 -2.5: 1}

In [43]:
import torch
if torch.tensor(data['train'][3][1])<0:
    print(1)

1


In [1]:
import pickle

with open("cmu_mosei.pkl",'br') as fr:
    data = pickle.load(fr)

In [6]:
data['train'][0][0]

(array(['key', 'is', 'part', 'of', 'the', 'people', 'that', 'we', 'use',
        'to', 'solve', 'those', 'issues', 'whether', "it's", 'stretch',
        'or', 'outdoor', 'resistance', 'or', 'abrasions', 'or',
        'different', 'technical', 'aspects', 'that', 'we', 'really',
        'need', 'to', 'solve', 'to', 'get', 'into', 'new', 'markets',
        "they've", 'been', 'able', 'to', 'bring', 'solutions'],
       dtype='<U10'),
 array([[ 2.56679929e-03, -1.55861712e+00,  3.23883057e+00, ...,
         -5.30693412e-01, -2.19982177e-01, -3.39928865e-01],
        [-9.00127828e-01,  4.08462316e-01,  4.10952941e-02, ...,
          3.32075864e-01,  1.19635546e+00, -1.06940329e+00],
        [ 1.53208494e+00, -1.17383730e+00,  5.54638326e-01, ...,
          1.13103139e+00,  1.12885392e+00, -1.34822011e+00],
        ...,
        [ 3.79706621e-01, -1.02476335e+00, -1.28982687e+00, ...,
         -6.92572296e-02,  5.84073551e-02,  3.85742486e-01],
        [ 7.13733375e-01, -2.56885111e-01, -1.558

### sentiment,happy,sad,anger,surprise,disgust,fear

In [33]:
torch.tensor(data['train'][13][1][0][1:])

tensor([0.0000, 0.6667, 0.0000, 0.0000, 0.6667, 0.0000])

In [42]:
torch.argmax(torch.tensor(data['train'][13][1][0][1:]))

tensor(4)

In [26]:
import torch

pred = torch.randn(1, 6, requires_grad=True)
target = torch.tensor(data['train'][13][1][0][1:]).unsqueeze(0)
crite = torch.nn.CrossEntropyLoss()
print(pred.shape)
print(target.shape)
loss = crite(pred,target)

torch.Size([1, 6])
torch.Size([1, 6])


RuntimeError: 1D target tensor expected, multi-target not supported

In [87]:
from torch import nn
loss = nn.CrossEntropyLoss()
input2 = torch.randn(4, 16, requires_grad=True).view(-1,2)
target = torch.empty((4,4,2), dtype=torch.long).random_(2).view(-1)
print(target)
print(input2)
print(input2.shape)
print(target.shape)
output = loss(input2, target)
output.backward()
print(output)

tensor([1, 0, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0,
        1, 1, 0, 0, 1, 0, 0, 0])
tensor([[ 0.6129,  0.2637],
        [ 0.8541, -0.1218],
        [-1.0926, -1.6378],
        [ 0.6312, -0.5633],
        [-0.6965,  1.0344],
        [ 0.3036,  0.3420],
        [ 0.5973, -3.2908],
        [-0.4144, -0.6295],
        [ 0.1794,  1.1225],
        [ 0.9076,  0.3090],
        [-0.9604, -0.2777],
        [-0.8041,  0.6001],
        [-0.3164,  1.0697],
        [-1.3966, -0.5272],
        [-0.1589, -2.0282],
        [ 0.4668,  0.1960],
        [ 0.7813,  0.7504],
        [-0.0417,  2.6000],
        [-1.0769,  0.2371],
        [-1.9157,  0.2623],
        [-0.5138,  0.3288],
        [ 0.3733,  2.0700],
        [-1.3352, -0.3285],
        [ 0.2220, -0.1354],
        [-0.5453,  2.2317],
        [-0.6583, -0.7996],
        [ 0.6352, -0.6070],
        [ 1.9906, -1.2194],
        [ 1.2246, -1.4058],
        [-0.3898, -1.7218],
        [ 1.7615,  1.1328],
        [-0.3582, -

In [65]:
import pickle

with open("cmu_mosei.pkl",'br') as fr:
    data = pickle.load(fr)

In [78]:
count=0
for i in range(len(data['train'])):
    if data['train'][i][1][0][1:][3]!=0:
        count+=1     
print(count)

1642
